<a href="https://colab.research.google.com/github/SmartGridsML/30daysML/blob/main/bilal_wav2vec2_finetune.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!add-apt-repository -y ppa:jonathonf/ffmpeg-4 && apt update && apt install -y ffmpeg
!pip install --quiet datasets transformers evaluate huggingface_hub jiwer

Repository: 'deb https://ppa.launchpadcontent.net/jonathonf/ffmpeg-4/ubuntu/ jammy main'
Description:
Backport of FFmpeg 4 and associated libraries. Now includes AOM/AV1 support!

FDK AAC is not compatible with GPL and FFmpeg can't be redistributed with it included. Please don't ask for it to be added to this public PPA.

---

PPA supporters:

BigBlueButton (https://bigbluebutton.org)

---

Donate to FFMPEG: https://ffmpeg.org/donations.html
Donate to Debian: https://www.debian.org/donations
Donate to this PPA: https://ko-fi.com/jonathonf
More info: https://launchpad.net/~jonathonf/+archive/ubuntu/ffmpeg-4
Adding repository.
Adding deb entry to /etc/apt/sources.list.d/jonathonf-ubuntu-ffmpeg-4-jammy.list
Adding disabled deb-src entry to /etc/apt/sources.list.d/jonathonf-ubuntu-ffmpeg-4-jammy.list
Adding key to /etc/apt/trusted.gpg.d/jonathonf-ubuntu-ffmpeg-4.gpg with fingerprint 4AB0F789CBA31744CC7DA76A8CF63AD3F06FC659
Get:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ In

In [2]:
from huggingface_hub import login

login()

In [3]:
!pip install librosa
!pip install datasets
!pip install huggingface_hub
!pip install huggingface-cli
!pip install -U accelerate
!pip install -U transformers
!pip install sagemaker

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.6/302.6 kB 5.8 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl (176.2 MB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-m

In [4]:
!echo "deb http://packages.cloud.google.com/apt gcsfuse-bionic main" > /etc/apt/sources.list.d/gcsfuse.list
!curl https://packages.cloud.google.com/apt/doc/apt-key.gpg | apt-key add -
!apt -qq update
!apt -qq install gcsfuse

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0Warning: apt-key is deprecated. Manage keyring files in trusted.gpg.d instead (see apt-key(8)).
100  2659  100  2659    0     0  36426      0 --:--:-- --:--:-- --:--:-- 36930
OK
W: http://packages.cloud.google.com/apt/dists/gcsfuse-bionic/InRelease: Key is stored in legacy trusted.gpg keyring (/etc/apt/trusted.gpg), see the DEPRECATION section in apt-key(8) for details.
E: The repository 'https://ppa.launchpadcontent.net/jonathonf/ffmpeg-4/ubuntu jammy Release' does not have a Release file.
The following NEW packages will be installed:
  gcsfuse
0 upgraded, 1 newly installed, 0 to remove and 45 not upgraded.
Need to get 10.5 MB of archives.
After this operation, 0 B of additional disk space will be used.
Selecting previously unselected package gcsfuse.
(

In [5]:
from google.colab import auth
auth.authenticate_user()

In [6]:
import os
import librosa
from datasets import Dataset, load_dataset
from huggingface_hub import notebook_login, create_repo
from datasets import Dataset, DatasetDict
import numpy as np

#Load & Prepare an Audio Dataset

In [7]:
#from datasets import load_dataset

#dataset = load_dataset("Shirali/ISSAI_KSC_335RS_v_1_1", split="train")
#iterable_dataset = dataset.to_iterable_dataset()
#dataset = load_dataset("Shirali/ISSAI_KSC_335RS_v_1_1", split="train",streaming=True, use_auth_token=True)

In [8]:
!mkdir -p /content/googleBucketFolder

In [9]:
#print(next(iter(dataset)))

In [10]:
!gcsfuse --implicit-dirs issai_ksc2 /content/googleBucketFolder

{"timestamp":{"seconds":1716835389,"nanos":506669383},"severity":"INFO","message":"Start gcsfuse/2.1.0 (Go version go1.22.3) for app \"\" using mount point: /content/googleBucketFolder\n"}
{"timestamp":{"seconds":1716835389,"nanos":506881757},"severity":"INFO","message":"GCSFuse mount command flags: {\"AppName\":\"\",\"Foreground\":false,\"ConfigFile\":\"\",\"MountOptions\":{},\"DirMode\":493,\"FileMode\":420,\"Uid\":-1,\"Gid\":-1,\"ImplicitDirs\":true,\"OnlyDir\":\"\",\"RenameDirLimit\":0,\"IgnoreInterrupts\":false,\"CustomEndpoint\":null,\"BillingProject\":\"\",\"KeyFile\":\"\",\"TokenUrl\":\"\",\"ReuseTokenFromUrl\":true,\"EgressBandwidthLimitBytesPerSecond\":-1,\"OpRateLimitHz\":-1,\"SequentialReadSizeMb\":200,\"AnonymousAccess\":false,\"MaxRetrySleep\":30000000000,\"StatCacheCapacity\":20460,\"StatCacheTTL\":60000000000,\"TypeCacheTTL\":60000000000,\"HttpClientTimeout\":0,\"MaxRetryDuration\":-1000000000,\"RetryMultiplier\":2,\"LocalFileCache\":false,\"TempDir\":\"\",\"ClientProto

In [11]:
!ls /content/googleBucketFolder/ISSAI_KSC2

Test  Test_flat  t_flat.zip  Train


In [12]:
#!tar -xzvf "/content/googleBucketFolder/ISSAI_KSC2.tar.gz" -C "/content/googleBucketFolder"

In [13]:
output_dir = "/content/googleBucketFolder/ISSAI_KSC2/Test_flat"

# code to flatten directory of test set to be used as full datatset
"""os.makedirs(output_dir, exist_ok=True)

# Iterate over the 6 subfolders
for subfolder in os.listdir(audio_dataset):
    subfolder_path = os.path.join(audio_dataset, subfolder)
    if os.path.isdir(subfolder_path):
        # Iterate over files in the subfolder
        for filename in os.listdir(subfolder_path):
            file_path = os.path.join(subfolder_path, filename)
            # Copy the file to the output directory
            shutil.copy(file_path, output_dir)"""

'os.makedirs(output_dir, exist_ok=True)\n\n# Iterate over the 6 subfolders\nfor subfolder in os.listdir(audio_dataset):\n    subfolder_path = os.path.join(audio_dataset, subfolder)\n    if os.path.isdir(subfolder_path):\n        # Iterate over files in the subfolder\n        for filename in os.listdir(subfolder_path):\n            file_path = os.path.join(subfolder_path, filename)\n            # Copy the file to the output directory\n            shutil.copy(file_path, output_dir)'

In [14]:
# Define a helper function to load audio and text files together
"""def load_data(file):
  # Extract filename from the path
  filename = os.path.basename(file["path"])

  # Assuming ".flac" comes before ".txt" in filenames
  audio_path = os.path.join(file["path"].replace(filename, filename.replace(".txt", ".flac")))
  text_path = file["path"]

  audio_data, _ = librosa.load(audio_path, sr=16000)  # Use librosa for audio loading
  with open(text_path, "r", encoding="utf-8") as f:
    text = f.read().strip()
  return {"audio": audio_data, "text": text}"""

  #return {"audio": audio_feature(audio_data), "text": text_feature(text)}

'def load_data(file):\n  # Extract filename from the path\n  filename = os.path.basename(file["path"])\n\n  # Assuming ".flac" comes before ".txt" in filenames\n  audio_path = os.path.join(file["path"].replace(filename, filename.replace(".txt", ".flac")))\n  text_path = file["path"]\n\n  audio_data, _ = librosa.load(audio_path, sr=16000)  # Use librosa for audio loading\n  with open(text_path, "r", encoding="utf-8") as f:\n    text = f.read().strip()\n  return {"audio": audio_data, "text": text}'

In [15]:
"""def load_data(data_dir):
    for filename in os.listdir(data_dir):
        if filename.endswith(".flac"):
            audio_file = os.path.join(data_dir, filename)
            text_file = os.path.join(data_dir, filename.replace(".flac", ".txt"))
            with open(text_file, "r") as f:
                text = f.read()
            audio, sr = librosa.load(audio_file, sr=16000)  # Load audio with a sampling rate of 16000
            [].append({"file": filename, "audio": audio, "text": text})
    return []"""
def load_data(data_dir):
    data = {}
    for filename in os.listdir(data_dir):
        if filename.endswith(".flac"):
            audio_file = os.path.join(data_dir, filename)
            text_file = os.path.join(data_dir, filename.replace(".flac", ".txt"))
            with open(text_file, "r") as f:
                text = f.read()
            audio, sr = librosa.load(audio_file, sr=16000)  # Load audio with a sampling rate of 16000
            # Convert audio to NumPy array
            audio_array = np.asarray(audio)
            data["audio"] =  {audio, {"text": text}}
    return data

In [16]:
def load_data_as_list(data_dir):
    """for filename in os.listdir(data_dir):
        if filename.endswith(".flac"):
            audio_file = os.path.join(data_dir, filename)
            text_file = os.path.join(data_dir, filename.replace(".flac", ".txt"))
            with open(text_file, "r") as f:
                text = f.read()
            audio, sr = librosa.load(audio_file, sr=16000)  # Load audio with a sampling rate of 16000
            [].append({"file": filename, "audio": audio, "text": text})
    return []"""
    data_list = []
    for filename in os.listdir(data_dir):
        if filename.endswith(".flac"):
            audio_file = os.path.join(data_dir, filename)
            text_file = os.path.join(data_dir, filename.replace(".flac", ".txt"))
            with open(text_file, "r") as f:
                text = f.read()
            audio, sr = librosa.load(audio_file, sr=16000)
            audio_array = np.asarray(audio)
            """data_dict = {

                "audio": audio_array,
                "text": text
            }#"file": audio_file,
            data_list.append(data_dict)"""
            data_list.append({"file": filename, "audio": audio_array, "text": text})
    return data_list

In [17]:
def load_dataset_from_folder(data_dir):
  """Loads data from a folder containing audio and text files.

  Args:
      data_dir: Path to the directory containing audio and text files.

  Returns:
      A DatasetDict containing the loaded data.
  """
  # Define features dictionary
  features = {
      "file": Dataset.Field(str, description="File name"),
      "audio": Dataset.Field(str, description="Path to audio file"),
      "text": Dataset.Field(str, description="Text content"),
  }

  # Split data into train and test sets based on naming convention
  # (assuming "train" or "test" is present in the file path)
  train_data = []
  test_data = []
  for filename in os.listdir(data_dir):
    if "train" in filename:
      audio_path = os.path.join(data_dir, filename)
      text_path = os.path.splitext(audio_path)[0] + ".txt"  # Replace .flac with .txt
      train_data.append({"file": filename, "audio": audio_path, "text": text_path})
    elif "test" in filename:
      audio_path = os.path.join(data_dir, filename)
      text_path = os.path.splitext(audio_path)[0] + ".txt"  # Replace .flac with .txt
      test_data.append({"file": filename, "audio": audio_path, "text": text_path})

  # Load datasets using in-memory data
  train_dataset = load_dataset("dummy", data=train_data, features=features)
  test_dataset = load_dataset("dummy", data=test_data, features=features)

  # Create DatasetDict
  dataset = DatasetDict({"train": train_dataset, "test": test_dataset})

  # Calculate number of rows for each split (optional)
  dataset.train.num_rows = len(train_data)
  dataset.test.num_rows = len(test_data)

  return dataset

# Load your data
data_dir = "/content/googleBucketFolder/ISSAI_KSC2/Test_flat"
dataset = load_dataset_from_folder(data_dir)

AttributeError: type object 'Dataset' has no attribute 'Field'

In [ ]:
# Define the base path to your dataset (adjust as needed)
data_dir = "/content/googleBucketFolder/ISSAI_KSC2/Test_flat"

In [ ]:
data = load_data(data_dir)

In [ ]:
#data['01_02_000.flac']

{'audio': array([ 0.00027466, -0.00030518, -0.00024414, ...,  0.01611328,
         0.00308228, -0.02502441], dtype=float32),
 'text': 'екі аяқты жұмыр басты пенделердің арасында түс көрмегендер қатары жоқ болар сірә'}

In [ ]:
data_list = load_data_as_list(data_dir)

In [ ]:
data_list[0]

{'audio': array([ 0.00027466, -0.00030518, -0.00024414, ...,  0.01611328,
         0.00308228, -0.02502441], dtype=float32),
 'text': 'екі аяқты жұмыр басты пенделердің арасында түс көрмегендер қатары жоқ болар сірә'}

In [ ]:
dataset = Dataset.from_list(data_list)

In [ ]:
(dataset["text"][0])

In [ ]:
#dataset = Dataset.from_list(data)
dataset = Dataset.from_dict(data)

In [ ]:
split_ds = dataset.train_test_split(test_size=0.2, seed=42)  # Split into train and test sets

dataset_dict = DatasetDict({
    "train": split_ds["train"],
    "test": split_ds["test"]
})

print(dataset_dict)

DatasetDict({
    train: Dataset({
        features: ['audio', 'text'],
        num_rows: 7480
    })
    test: Dataset({
        features: ['audio', 'text'],
        num_rows: 1871
    })
})


In [ ]:
print(dataset_dict)

DatasetDict({
    train: Dataset({
        features: ['audio', 'text'],
        num_rows: 7480
    })
    test: Dataset({
        features: ['audio', 'text'],
        num_rows: 1871
    })
})


In [ ]:
from huggingface_hub import notebook_login
notebook_login()

In [ ]:
# Combine train and test datasets for upload
"""dataset_dict.push_to_hub("BilalS96/ISSAI_KSC2")
dataset_dict["train"].push_to_hub("BilalS96/ISSAI_KSC2", split="train")
dataset_dict["test"].push_to_hub("BilalS96/ISSAI_KSC2", split="test")"""


Uploading the dataset shards:   0%|          | 0/6 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

...

Uploading the dataset shards:   0%|          | 0/2 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/439 [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/datasets/BilalS96/ISSAI_KSC2/commit/ee9732d4622cc8860dac97ada7f06d6d9ca38608', commit_message='Upload dataset', commit_description='', oid='ee9732d4622cc8860dac97ada7f06d6d9ca38608', pr_url=None, pr_revision=None, pr_num=None)

In [ ]:
len(dataset_dict["train"])

7480

In [ ]:
"""
def create_dataset(split):
  # Get all subdirectories within the specified split directory
  subdirs = [os.path.join(data_dir, split, subdir) for subdir in os.listdir(os.path.join(data_dir, split))]

  # List audio and text file paths based on your structure
  data_files = []
  for subdir in subdirs:
    for filename in os.listdir(subdir):
      if filename.endswith(".txt"):
        data_files.append({"path": os.path.join(subdir, filename)})

  return Dataset.from_pandas(pd.DataFrame(data_files))"""

In [ ]:
"""notebook_login()

create_repo("BilalS96/ISSAI_KSC2", repo_type="dataset")

train_test, test_dataset = dataset.train_test_split(test_size=0.2)
dataset = DatasetDict({
    'train': train_test['train'],
    'test': train_test['test']})

# Combine train and test datasets for upload
msg_ds = train_test.concat(test_dataset)

msg_ds.push_to_hub("BilalS96/ISSAI_KSC2", private=True)"""
#print(f"Dataset uploaded to Hugging Face Datasets: {dataset_name}")

In [ ]:
"""from datasets import load_dataset
hf_dataset = load_dataset("BilalS96/ISSAI_KSC2")"""

In [ ]:
def preprocess_data(sample):
    # Load the audio file
    audio_path = os.path.join(data_dir, sample["file"].replace(".txt", ".flac"))
    audio_data, sampling_rate = librosa.load(audio_path, sr=16000)

    # Load the text file
    text_path = os.path.join(data_dir, sample["file"])
    with open(text_path, "r", encoding="utf-8") as f:
        text = f.read().strip()

    # Create the desired data structure
    sample = {
        "file": sample["file"],
        "audio": {
            "path": sample["file"].replace(".txt", ".flac"),
            "array": audio_data,
            "sampling_rate": sampling_rate,
        },
        "text": text,
    }

    return sample

In [ ]:
processed_data = []

for filename in os.listdir(data_dir):
  # Check if it's a text file
  if filename.endswith(".txt"):
    file_path = os.path.join(data_dir, filename)

    # Call load_data function with a dictionary containing path information
    data_point = load_data({"path": file_path})
    processed_data.append(data_point)

In [ ]:
# Split the dataset into train and test sets
train_dataset, test_dataset = dataset.train_test_split(test_size=0.2, seed=42)

# Create a DatasetDict to store train and test sets
dataset = DatasetDict({
    'train': train_dataset,
    'test': test_dataset
})

## Load Dataset

In [ ]:
issai = load_dataset("BilalS96/ISSAI_KSC2")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Generating train split:   0%|          | 0/7480 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1871 [00:00<?, ? examples/s]

In [18]:
issai_train = load_dataset("BilalS96/ISSAI_KSC2", split="train")
issai_test = load_dataset("BilalS96/ISSAI_KSC2", split="test")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Generating train split:   0%|          | 0/7480 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1871 [00:00<?, ? examples/s]

In [19]:
len(issai_train)

7480

In [20]:
import IPython.display as ipd
import pandas as pd

sample = next(iter(issai_train))
audio = sample["audio"]
print(sample["text"])


бұл мәселе бойынша сөз халықаралық істер қорғаныс және қауіпсіздік комитетінің төрағасы депутат ерман мұхтар тілдәбекұлына беріледі


In [21]:
ipd.Audio(data=audio, autoplay=True, rate=16000)

In [22]:
import random
from IPython.display import display, HTML
import pandas as pd

def show_random_elements(dataset, num_examples=10):
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."
    picks = []
    for _ in range(num_examples):
        pick = random.randint(0, len(dataset)-1)
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)
        picks.append(pick)

    df = pd.DataFrame(dataset[picks])
    display(HTML(df.to_html()))

In [25]:
show_random_elements(issai_train)

## Pre-Process the Dataset

In [26]:
# We can set the sampling rate of our audio dataset through the cast_column method.
# This doesn't change the dataset in-place, but resamples the dataset on
# the fly the first time a sample is loaded.
from datasets import Audio

#dataset = dataset.cast_column("audio", Audio(sampling_rate=16000))

##Create Vocab File

In [27]:
print(sample)

{'audio': [0.00213623046875, 0.00177001953125, 0.00018310546875, -0.001678466796875, -0.002044677734375, 0.00335693359375, 0.001251220703125, -0.00506591796875, -0.0081787109375, -0.007781982421875, -0.00616455078125, -0.00799560546875, -0.00677490234375, 0.0010986328125, 0.003204345703125, 0.0018310546875, 0.003936767578125, 0.00396728515625, 0.004364013671875, 0.001007080078125, -0.000457763671875, 0.00152587890625, -0.0013427734375, -0.00146484375, -0.0001220703125, -0.001068115234375, -0.002899169921875, -0.008544921875, -0.011199951171875, -0.0050048828125, -0.0020751953125, 0.00030517578125, 0.00225830078125, 0.00384521484375, 0.005157470703125, 0.002227783203125, -0.0018310546875, -0.00335693359375, -0.00726318359375, -0.008819580078125, -0.00384521484375, -0.002838134765625, -0.00390625, -0.00469970703125, -0.002777099609375, 3.0517578125e-05, 6.103515625e-05, -0.0008544921875, 0.0029296875, 0.00439453125, 0.00128173828125, -0.0001220703125, -0.001190185546875, -0.0017700195312

In [28]:
import re
chars_to_ignore_regex = '[\,\?\.\!\-\;\:\"]'

def remove_special_characters(batch):
    batch["text"] = re.sub(chars_to_ignore_regex, '', batch["text"]).lower()
    return batch

In [29]:
#dataset = dataset.map(remove_special_characters)
issai_train = issai_train.map(remove_special_characters)
issai_test = issai_test.map(remove_special_characters)

Map:   0%|          | 0/7480 [00:00<?, ? examples/s]

Map:   0%|          | 0/1871 [00:00<?, ? examples/s]

In [30]:
def extract_all_chars(batch):
    batch_vocabs = []
    batch_all_text = []

    for text in batch["text"]:
        if text:
            all_text = "".join(text)
            vocab = list(set(all_text))
            batch_vocabs.append(vocab)
            batch_all_text.append(all_text)
        else:
            batch_vocabs.append([])
            batch_all_text.append("")

    return {"vocab": batch_vocabs, "all_text": batch_all_text}

In [31]:
def extract_all_chars(batch):
  # Handle empty batches gracefully
  if not batch["text"]:
      return {"vocab": [], "all_text": []}  # Return empty lists

  # Concatenate text from all samples in the batch
  all_text = "".join(batch["text"])

  # Extract unique characters
  vocab = list(set(all_text))
  return {"vocab": [vocab], "all_text": [all_text]}


In [32]:
vocab_train = issai_train.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns= issai_train.column_names)
vocab_test = issai_test.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns= issai_test.column_names)

Map:   0%|          | 0/7480 [00:00<?, ? examples/s]

Map:   0%|          | 0/1871 [00:00<?, ? examples/s]

In [33]:
vocab_list = list(set(vocab_train["vocab"][0]) | set(vocab_test["vocab"][0]))

In [34]:
vocab_dict = {v: k for k, v in enumerate(sorted(vocab_list))}


In [35]:
vocab_dict["|"] = vocab_dict[' ']
del vocab_dict[' ']

In [36]:
vocab_dict["[UNK]"] = len(vocab_dict)
vocab_dict["[PAD]"] = len(vocab_dict)

In [37]:
vocab_dict

{'а': 1,
 'б': 2,
 'в': 3,
 'г': 4,
 'д': 5,
 'е': 6,
 'ж': 7,
 'з': 8,
 'и': 9,
 'й': 10,
 'к': 11,
 'л': 12,
 'м': 13,
 'н': 14,
 'о': 15,
 'п': 16,
 'р': 17,
 'с': 18,
 'т': 19,
 'у': 20,
 'ф': 21,
 'х': 22,
 'ц': 23,
 'ч': 24,
 'ш': 25,
 'щ': 26,
 'ъ': 27,
 'ы': 28,
 'ь': 29,
 'э': 30,
 'ю': 31,
 'я': 32,
 'і': 33,
 'ғ': 34,
 'қ': 35,
 'ң': 36,
 'ү': 37,
 'ұ': 38,
 'һ': 39,
 'ә': 40,
 'ө': 41,
 '|': 0,
 '[UNK]': 42,
 '[PAD]': 43}

In [38]:
import json
with open('vocab.json', 'w') as vocab_file:
    json.dump(vocab_dict, vocab_file)

## Tokenizer


Define a data collator. In contrast to most NLP models, XLSR-Wav2Vec2 has a much larger input length than output length. E.g., a sample of input length 50000 has an output length of no more than 100. Given the large input sizes, it is much more efficient to pad the training batches dynamically meaning that all training samples should only be padded to the longest sample in their batch and not the overall longest sample. Therefore, fine-tuning XLSR-Wav2Vec2 requires a special padding data collator, which we will define below

Evaluation metric. During training, the model should be evaluated on the word error rate. We should define a compute_metrics function accordingly

Load a pretrained checkpoint. We need to load a pretrained checkpoint and configure it correctly for training.

Define the training configuration.

In [39]:
from transformers import Wav2Vec2ForCTC
from transformers import Wav2Vec2CTCTokenizer
import torch
from datasets import load_metric
from dataclasses import dataclass, field
from typing import Any, Dict, List, Optional, Union

In [40]:
from transformers import Wav2Vec2CTCTokenizer, Wav2Vec2FeatureExtractor, Wav2Vec2Processor

tokenizer = Wav2Vec2CTCTokenizer("./vocab.json", unk_token="[UNK]",
                                 pad_token="[PAD]", word_delimiter_token="|")

# create Wav2Vec2 feature extractor
feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000,
                                             padding_value=0.0, do_normalize=True, return_attention_mask=False)
# create a processor pipeline
processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

In [43]:
repo_name = "wav2vec2-base-issai-colab"


In [47]:
from huggingface_hub import logging
login()

In [48]:
tokenizer.push_to_hub(repo_name)


CommitInfo(commit_url='https://huggingface.co/Kamshat/wav2vec2-base-issai-colab/commit/230b11ecdd5e2d0ce6c7fcbabff6359695cb5089', commit_message='Upload tokenizer', commit_description='', oid='230b11ecdd5e2d0ce6c7fcbabff6359695cb5089', pr_url=None, pr_revision=None, pr_num=None)

In [49]:
def prepare_dataset(batch):
    audio = batch["audio"]

    # batched output is "un-batched"
    batch["input_values"] = processor(audio, sampling_rate=16000).input_values[0]
    batch["input_length"] = len(batch["input_values"])

    with processor.as_target_processor():
        batch["labels"] = processor(batch["text"]).input_ids
    return batch




In [50]:
issai_train = issai_train.map(prepare_dataset, remove_columns=issai_train.column_names)
issai_test = issai_test.map(prepare_dataset, remove_columns=issai_test.column_names)

Map:   0%|          | 0/7480 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/transformers/models/wav2vec2/processing_wav2vec2.py:156: UserWarning: `as_target_processor` is deprecated and will be removed in v5 of Transformers. You can process your labels by using the argument `text` of the regular `__call__` method (either in the same call as your audio inputs, or in a separate call.
  warnings.warn(


Map:   0%|          | 0/1871 [00:00<?, ? examples/s]

In [51]:
@dataclass
class DataCollatorCTCWithPadding:
    """
    Data collator that will dynamically pad the inputs received.
    Args:
        processor (:class:`~transformers.Wav2Vec2Processor`)
            The processor used for proccessing the data.
        padding (:obj:`bool`, :obj:`str` or :class:`~transformers.tokenization_utils_base.PaddingStrategy`, `optional`, defaults to :obj:`True`):
            Select a strategy to pad the returned sequences (according to the model's padding side and padding index)
            among:
            * :obj:`True` or :obj:`'longest'`: Pad to the longest sequence in the batch (or no padding if only a single
              sequence if provided).
            * :obj:`'max_length'`: Pad to a maximum length specified with the argument :obj:`max_length` or to the
              maximum acceptable input length for the model if that argument is not provided.
            * :obj:`False` or :obj:`'do_not_pad'` (default): No padding (i.e., can output a batch with sequences of
              different lengths).
        max_length (:obj:`int`, `optional`):
            Maximum length of the ``input_values`` of the returned list and optionally padding length (see above).
        max_length_labels (:obj:`int`, `optional`):
            Maximum length of the ``labels`` returned list and optionally padding length (see above).
        pad_to_multiple_of (:obj:`int`, `optional`):
            If set will pad the sequence to a multiple of the provided value.
            This is especially useful to enable the use of Tensor Cores on NVIDIA hardware with compute capability >=
            7.5 (Volta).
    """

    processor: Wav2Vec2Processor
    padding: Union[bool, str] = True
    max_length: Optional[int] = None
    max_length_labels: Optional[int] = None
    pad_to_multiple_of: Optional[int] = None
    pad_to_multiple_of_labels: Optional[int] = None

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lenghts and need
        # different padding methods
        input_features = [{"input_values": feature["input_values"]} for feature in features]
        label_features = [{"input_ids": feature["labels"]} for feature in features]

        batch = self.processor.pad(
            input_features,
            padding=self.padding,
            max_length=self.max_length,
            pad_to_multiple_of=self.pad_to_multiple_of,
            return_tensors="pt",
        )
        with self.processor.as_target_processor():
            labels_batch = self.processor.pad(
                label_features,
                padding=self.padding,
                max_length=self.max_length_labels,
                pad_to_multiple_of=self.pad_to_multiple_of_labels,
                return_tensors="pt",
            )

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        batch["labels"] = labels

        return batch

In [52]:
data_collator = DataCollatorCTCWithPadding(processor=processor, padding=True)

In [53]:
!pip install jiwer

In [54]:
wer_metric = load_metric("wer")

<ipython-input-54-605de035dfd7>:1: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  wer_metric = load_metric("wer")
/usr/local/lib/python3.10/dist-packages/datasets/load.py:759: FutureWarning: The repository for wer contains custom code which must be executed to correctly load the metric. You can inspect the repository content at https://raw.githubusercontent.com/huggingface/datasets/2.19.1/metrics/wer/wer.py
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this metric from the next major release of `datasets`.
  warnings.warn(


In [55]:
def compute_metrics(pred):
    pred_logits = pred.predictions
    pred_ids = np.argmax(pred_logits, axis=-1)

    pred.label_ids[pred.label_ids == -100] = processor.tokenizer.pad_token_id

    pred_str = processor.batch_decode(pred_ids)
    # we do not want to group tokens when computing the metrics
    label_str = processor.batch_decode(pred.label_ids, group_tokens=False)

    wer = wer_metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}

## Load a Pre-Trained Checkpoint


In [56]:
model = Wav2Vec2ForCTC.from_pretrained(
    "facebook/wav2vec2-large-xlsr-53",
    attention_dropout=0.1,
    hidden_dropout=0.1,
    feat_proj_dropout=0.0,
    mask_time_prob=0.05,
    layerdrop=0.1,
    ctc_loss_reduction="mean",
    pad_token_id=processor.tokenizer.pad_token_id,
    vocab_size=len(processor.tokenizer)
)

config.json:   0%|          | 0.00/1.77k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.27G [00:00<?, ?B/s]

Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at facebook/wav2vec2-large-xlsr-53 and are newly initialized: ['lm_head.bias', 'lm_head.weight', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original1']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [59]:
from transformers import TrainingArguments

training_args = TrainingArguments(
  output_dir=repo_name,
  group_by_length=True,
  per_device_train_batch_size=4,
  gradient_accumulation_steps=2,
  evaluation_strategy="steps",
  num_train_epochs=30,
  gradient_checkpointing=True,
  fp16=True,
  save_steps=400,
  save_total_limit=2,
  eval_steps=400,
  logging_steps=400,
  learning_rate=3e-4,
  warmup_steps=500,
  push_to_hub=True,
)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1474: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [60]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    data_collator=data_collator,
    args=training_args,
    compute_metrics=compute_metrics,
    train_dataset=issai_train,
    eval_dataset=issai_test,
    tokenizer=processor.feature_extractor,
)

In [62]:
trainer.train(resume_from_checkpoint=None)

/usr/local/lib/python3.10/dist-packages/transformers/models/wav2vec2/processing_wav2vec2.py:156: UserWarning: `as_target_processor` is deprecated and will be removed in v5 of Transformers. You can process your labels by using the argument `text` of the regular `__call__` method (either in the same call as your audio inputs, or in a separate call.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:464: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


/usr/local/lib/python3.10/dist-packages/torch/nn/modules/conv.py:306: UserWarning: Plan failed with a cudnnException: CUDNN_BACKEND_EXECUTION_PLAN_DESCRIPTOR: cudnnFinalize Descriptor Failed cudnn_status: CUDNN_STATUS_NOT_SUPPORTED (Triggered internally at ../aten/src/ATen/native/cudnn/Conv_v8.cpp:919.)
  return F.conv1d(input, weight, bias, self.stride,
/usr/local/lib/python3.10/dist-packages/transformers/models/wav2vec2/processing_wav2vec2.py:156: UserWarning: `as_target_processor` is deprecated and will be removed in v5 of Transformers. You can process your labels by using the argument `text` of the regular `__call__` method (either in the same call as your audio inputs, or in a separate call.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:464: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, bu

TrainOutput(global_step=28050, training_loss=0.6754494413420054, metrics={'train_runtime': 59214.0901, 'train_samples_per_second': 3.79, 'train_steps_per_second': 0.474, 'total_flos': 4.209099233760768e+19, 'train_loss': 0.6754494413420054, 'epoch': 30.0})

In [63]:
kwargs = {
    "dataset_tags": "ISSAI_KSC2",
    "dataset": "BilalS96/ISSAI_KSC2",  # a 'pretty' name for the training dataset
    "dataset_args": "config: kzk, split: test",
    "language": "kz",
    "model_name": "Kammi",
    "finetuned_from": "facebook/wav2vec2-large-xlsr-53",
    "tasks": "automatic-speech-recognition",
    "tags": "hf-asr-leaderboard",
}

In [64]:
trainer.push_to_hub(**kwargs)

Upload 2 LFS files:   0%|          | 0/2 [00:00<?, ?it/s]

model.safetensors:   0%|          | 0.00/1.26G [00:00<?, ?B/s]

events.out.tfevents.1716838729.ee6fa7619648.1339.0:   0%|          | 0.00/44.2k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/Kamshat/wav2vec2-base-issai-colab/commit/c8bdc4340f07026a8b4bafa924771379905b0dc0', commit_message='End of training', commit_description='', oid='c8bdc4340f07026a8b4bafa924771379905b0dc0', pr_url=None, pr_revision=None, pr_num=None)